#### Q1

##### 导入科学包

In [2]:
import os
import pandas as pd
import create_db
import create_table
import import_to_table
import venue_scan_import

##### 建立数据库并，创建表格并导入数据，第一次运行请取消注释

In [3]:
'''
Those files are required to run exact one time
'''
# create_db.main()
# create_table.main()
# import_to_table.main()
# venue_scan_import.main()

'\nThose files are required to run exact one time\n'

### 数据预处理

##### 从csv文件读取相关数据

acid_sample_info: 核酸采样信息

person_info: 所有人员信息

personal_report_info: 个人上报信息

vaccination_info: 疫苗接种信息

venue_info: 所有场所信息

In [4]:
files_path = 'C:/Users/Deng_/Desktop/datas/'
acid_sample_info = pd.read_csv(files_path+'acid_sample_info.csv')
person_info = pd.read_csv(files_path+'person_info.csv')
personal_report_info = pd.read_csv(files_path+'personal_report_info.csv')
vaccination_info = pd.read_csv(files_path+'vaccination_info.csv')
venue_info = pd.read_csv(files_path+'venue_info.csv')

##### 链接本地数据库

In [5]:
import pymysql
db = pymysql.connect(
    host='localhost',
    user='root',
    password='ff2017',
    charset='utf8',
    database='tedi_data'
)

##### 通过sql快速获取阳性人员的出行信息

In [6]:
## 获取阳性人员的出行数据
q = '''
select * from pos_travel_info'''
pos_travel_info = pd.read_sql(q,con=db)

C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\3921939915.py:4: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  pos_travel_info = pd.read_sql(q,con=db)


##### 获取阳性人员的核酸采样信息

In [7]:
acid_pos = acid_sample_info.drop(acid_sample_info[acid_sample_info['jg'] == '阴性'].index)
acid_pos = acid_pos.drop(acid_sample_info[acid_sample_info['jg'] == '未知'].index)
acid_pos = acid_pos[['user_id', 'cysj', 'grid_point_id']]

In [8]:
pos_travel_info[pos_travel_info['grid_id']==1539]

uid                date  grid_id
5068     3492 2022-11-13 10:54:12     1539
12661    6632 2022-10-22 16:10:22     1539
14137    7685 2022-10-01 10:04:23     1539
17237    9202 2022-11-01 18:50:35     1539
18791    9962 2022-10-30 08:07:46     1539
24914   13286 2022-10-12 13:52:00     1539
28280   15081 2022-11-19 15:35:25     1539
29614   15694 2022-11-25 18:58:08     1539
32954   17672 2022-11-24 16:35:09     1539
42597   23784 2022-10-04 17:52:50     1539
42896   24060 2022-11-07 22:20:18     1539
48302   27051 2022-11-03 10:00:48     1539
49036   27427 2022-10-14 04:58:29     1539
63158   35353 2022-11-19 15:00:35     1539
72025   40215 2022-11-12 12:49:18     1539
73406   40803 2022-11-15 18:22:09     1539
78857   43758 2022-10-13 20:22:15     1539
78881   43758 2022-10-19 07:39:09     1539
81157   45376 2022-10-23 23:54:17     1539
83544   46424 2022-11-21 23:08:46     1539
84390   46995 2022-11-12 07:04:14     1539
103852  58266 2022-11-20 13:32:41     1539
110543  62025 2022-10-25 20:35:57     1539
118854  66838 2022-10-22 13:39:29     1539
127177  70880 2022-10-04 13:06:35     1539
131913  72990 2022-10-05 12:38:44     1539
133371  73855 2022-10-27 14:34:59     1539
138056  77018 2022-11-08 11:26:05     1539
142529  78712 2022-11-17 13:02:51     1539
157433  86032 2022-10-01 09:59:32     1539
158848  86773 2022-10-05 13:41:43     1539
160885  87852 2022-11-26 18:00:01     1539

In [9]:
## 时间取整
for i in acid_pos['cysj'].index:
    acid_pos['cysj'][i] = acid_pos['cysj'][i][:10]

C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\632512544.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  acid_pos['cysj'][i] = acid_pos['cysj'][i][:10]


In [10]:
prepath = 'C:/Users/Deng_/PycharmProjects/test_for_tedi/tedi-230412/datas/venue_code_info/'
files = os.listdir(prepath)

##### 开始查找密接者
结果表格式:  '序号', '密接者ID', '密接日期', '密接场所ID', '阳性人员ID'

关键变量定义:
* idx: 用于记录产生的密接者数量，用于作为result中的序号

* acid_pos: 在61天内核酸检测出现过阳性的人员的数据，包含人员ID，核酸采样时间和采样地点，我们此处仅使用unique的人员ID作遍历源，部分字段用作结果标中的阳性人员ID一列

* pos_travel_info: 在61天内阳性人员的活动信息，来源于场所扫码信息，包含人员ID，出行时间按（date）和对应出行地点（grid_id），部分字段用于结果表中的密接时间一列

* df_scan: 某个核酸检测结果为阳性，在检测出阳的前两天（共三天）的所有场所扫码信息，其中部分非阳人员ID字段将用于结果表中密接者ID一列

* current_pos_grid: 遍历过程中的变量，每一次取当前阳性人员在某一时间段去过的所有场所ID，此时间段与df_scan的时间段一致，部分字段用于结果表中密接场所ID一列


##### 寻找思路：
1. 对于每一个阳性人员id，使用acid_pos变量可以获取对应检测出为阳性时间，该时间往前推移2天，可以获得一个时间范围 t_range
2. 对于每一个阳性人员id，使用pos_travel_info变量获取 t_range 时间范围内该id所有出行地点，即变量 current_pos_grid
3. 遍历所有阳性人员id，根据id取出该id 在 date_range 时间内出行信息，嵌套遍历所有出行信息
4. 使用场所扫码信息表，每次读取 t_range 时间范围内的数据
5. 在读取的数据中，筛去所有阳性人员得到剩余数据，即当前时间内非阳人员，寻找 场所id等于阳性人员出行id 的数据，此时找到一个阳性人员在一个地点对应时间段的密接者，存入结果df

In [ ]:
idx = 1
# 初始化结果DataFrame
result1 = pd.DataFrame(columns=['序号', '密接者ID', '密接日期', '密接场所ID', '阳性人员ID'])
for i in acid_pos.index:
    Y_id = acid_pos['user_id'][i]
    print("pos_id: ", Y_id)
    Y_time = pd.to_datetime(acid_pos['cysj'][i], format='%Y-%m-%d')

    start_time = Y_time - pd.Timedelta(days=2)
    for epoch in range(len(files)):
        file_name = files[epoch]
        s = "".join(str(start_time)[:10].split('-'))
        if Y_time > pd.to_datetime('2022-11-30', format='%Y-%m-%d'): e = '20221130'
        else: e = "".join(str(Y_time)[:10].split('-'))
        start = files.index(s+'.csv')
        end = files.index(e+'.csv')

    for epoch in range(start, end+1):
        ## 某一天的数据
        file_name = files[epoch]
        df_scan = pd.read_csv(prepath+file_name)
        df_scan = df_scan[['grid_point_id','user_id','create_time']]
        df_scan = df_scan[df_scan['user_id']!=Y_id] ## 排除阳性人员本身

        ## 寻找当前阳性人员在该时间段去过的场所id
        current_pos_grid = pos_travel_info [(pos_travel_info['uid']==Y_id)]
        this_day_start = start_time
        this_day_end = start_time + pd.Timedelta(days=1)
        current_pos_grid = current_pos_grid [(pd.to_datetime(current_pos_grid['date'])<=this_day_end) & (pd.to_datetime(current_pos_grid['date'])>=this_day_start)]
        current_pos_grid = current_pos_grid[['grid_id','uid']]

        df_scan = df_scan[ df_scan['grid_point_id'].isin(current_pos_grid['grid_id'].tolist()) ]

        if df_scan.empty or current_pos_grid.empty: continue
        else:
            df_scan.drop_duplicates(subset=['user_id'],inplace = True)
            for _, ROW in df_scan.iterrows():
                grid_id = ROW[0]
                user_id = ROW[1]
                contact = ROW[2]
                for _, row in current_pos_grid.iterrows():
                    y_id = row[1]
                    y_grid = row[0]
                    if y_grid == grid_id:
                        result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
                        idx+=1


C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\A

pos_id:  33246
pos_id:  13586
pos_id:  12447


C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\A

pos_id:  87952


C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\AppData\Local\Temp\ipykernel_5608\2405172286.py:45: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  result1 = result1.append({'序号': idx, '密接者ID':user_id ,'密接日期': contact, '密接场所ID': grid_id, '阳性人员ID': Y_id}, ignore_index=True)
C:\Users\Deng_\A

In [ ]:
result1

In [40]:
# 保存结果到文件
result1.to_csv('result1.csv', index=False)

#### Q2

##### 开始查找次密接者
结果表格式:  '序号', '次密接者ID', '次密接日期', '次密接场所ID', '密接人员ID'

关键变量定义:
* idx: 用于记录产生的次密接者数量，用于作为result中的序号

* close_contact: 第一问获得的密接人员id，我们此处仅使用unique的人员ID作遍历源，部分字段用作结果标中的密接人员ID一列

* con_travel_info: 在61天密接人员的活动信息，来源于场所扫码信息，包含人员ID，出行时间按（date）和对应出行地点（grid_id），部分字段用于结果表中的次密接时间一列

* df_scan: 某位密接者，在被检测为密接者的前两天（共三天）的所有场所扫码信息，其中部分非密接人员ID字段将用于结果表中次密接者ID一列

* current_con_grid: 遍历过程中的变量，每一次取当前密接人员在某一时间段去过的所有场所ID，此时间段与df_scan的时间段一致，部分字段用于结果表中次密接场所ID一列


##### 寻找思路：
1. 对于每一个密接人员id，使用close_contact变量可以获取对应id判定为密接者时间，该时间往前推移2天，可以获得一个时间范围 t_range
2. 对于每一个密接人员id，使用con_travel_info变量获取 t_range 时间范围内该id所有出行地点，即变量 current_con_grid
3. 遍历所有密接人员id，根据id取出该id 在 date_range 时间内出行信息，嵌套遍历所有出行信息
4. 使用场所扫码信息表，每次读取 t_range 时间范围内的数据
5. 在读取的数据中，筛去所有密接人员，得到非密接者数据，寻找 场所id等于密接人员出行id 的数据，此时找到一个密接人员在一个地点对应时间段的次密接者，存入结果df

In [37]:
## 获取密接的出行数据
q = '''
select * from contact_travel_info'''
con_travel_info = pd.read_sql(q,con=db)

C:\Users\Deng_\AppData\Local\Temp\ipykernel_11316\2816564333.py:4: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  con_travel_info = pd.read_sql(q,con=db)


In [17]:
con_travel_info

uid                date  grid_id
0           10 2022-10-01 13:45:43     2285
1           10 2022-10-01 12:26:43      855
2           10 2022-10-01 14:02:43     2232
3           10 2022-10-02 11:17:35      397
4           10 2022-10-02 17:57:35     2285
...        ...                 ...      ...
2359789  99885 2022-11-26 15:56:03     2143
2359790  99885 2022-11-26 20:35:03     2055
2359791  99885 2022-11-27 13:46:19     2816
2359792  99885 2022-11-27 11:41:19     2179
2359793  99885 2022-11-27 14:06:19     2055

[2359794 rows x 3 columns]

In [23]:
idx = 0
result2 = pd.DataFrame(columns=['序号', '次密接者ID', '次密接日期', '次密接场所ID', '密接者ID'])
close_contact = pd.read_csv("C:/Users/Deng_/PycharmProjects/test_for_tedi/tedi-230412/result1.csv")

In [24]:
close_contact

序号  密接者ID                 密接日期  密接场所ID  阳性人员ID
0          1     10  2022-10-02 17:57:35    2285   85294
1          2  10019  2022-10-02 22:33:17    2232   85294
2          3  10020  2022-10-03 02:14:20    2285   85294
3          4  10032  2022-10-02 15:13:04    2232   85294
4          5  10063  2022-10-02 20:00:11    2232   85294
...      ...    ...                  ...     ...     ...
99992  99993  99992  2022-11-04 21:41:11    2173    5225
99993  99994  99994  2022-11-02 19:18:04    1517   27962
99994  99995  99994  2022-11-05 13:36:00    1164   75738
99995  99996  99996  2022-11-05 19:09:28    2285   43541
99996  99997  99996  2022-11-05 15:22:28     102   89259

[99997 rows x 5 columns]

In [ ]:
for i in close_contact.index:
    contact_id = close_contact['密接者ID'][i]
    print("contact_id: ", contact_id)
    contact_time = pd.to_datetime(close_contact['密接日期'][i], format='%Y-%m-%d')
    start_time = contact_time - pd.Timedelta(days=2)
    for epoch in range(len(files)):
        file_name = files[epoch]
        s = "".join(str(start_time)[:10].split('-'))
        if contact_time > pd.to_datetime('2022-11-30', format='%Y-%m-%d'): e = '20221130'
        else: e = "".join(str(contact_time)[:10].split('-'))
        if s=='20220930': s = '20221001'
        start = files.index(s+'.csv')
        end = files.index(e+'.csv')

    for epoch in range(start, end+1):
        ## 某一天的数据
        file_name = files[epoch]
        df_scan = pd.read_csv(prepath+file_name)
        df_scan = df_scan[['grid_point_id','user_id','create_time']]
        df_scan = df_scan[df_scan['user_id']!=contact_id] ## 排除密接者本身

        ## 寻找当前密接者人员在该时间段去过的场所id
        current_con_grid = con_travel_info [(con_travel_info['uid']==contact_id)]
        this_day_start = start_time
        this_day_end = start_time + pd.Timedelta(days=1)
        current_con_grid = current_con_grid[(pd.to_datetime(current_con_grid['date'])<=this_day_end) & (pd.to_datetime(current_con_grid['date'])>=this_day_start)]
        current_con_grid = current_con_grid[['grid_id','uid']]

        ## 找到在对应时间去过该地点的扫码信息
        df_scan = df_scan[ df_scan['grid_point_id'].isin(current_con_grid['grid_id'].tolist()) ]
        if df_scan.empty or current_con_grid.empty: continue
        else:
            df_scan.drop_duplicates(subset=['user_id'],inplace = True)
            current_con_grid.drop_duplicates(subset=['grid_id'],inplace = True)
            for _, ROW in df_scan.iterrows():
                grid_id = ROW[0]
                user_id = ROW[1]
                contact = ROW[2]
                for _, row in current_con_grid.iterrows():
                    c_grid = row[0]
                    if c_grid == grid_id and user_id not in result2['次密接者ID'].to_list():
                        result2 = result2.append({'序号': idx, '次密接者ID':user_id ,'次密接日期': contact, '次密接场所ID': grid_id, '密接者ID': contact_id}, ignore_index=True)
                        idx+=1


In [ ]:
# 保存结果到文件
result2.to_csv('result2.csv', index=False)